# Tutorial 2 - Mass action kinetics

In [ ]:
# preliminaries
%matplotlib widget
import numpy as np
import scipy as sp
import pandas as pd
import scipy.optimize
import pysces
from matplotlib import pyplot as plt
import os
import copy
from lmfit import Model
backupdir = os.getcwd()

## Question 2

In [ ]:
mod = pysces.model('massaction', '.')

In [ ]:
mod.doSim(end=0.5, points=30)

In [ ]:
mod.sim

In [ ]:
mod.SimPlot()

In [ ]:
f, ax = plt.subplots()
ax.plot(mod.sim.Time, mod.sim.A, label='a')
ax.plot(mod.sim.Time, mod.sim.B, label='b')
ax.plot(mod.sim.Time, mod.sim.C, label='c')
ax.set_xlabel('Time (s)')
ax.set_ylabel('Concentration (M)')
ax.legend()

In [ ]:
plt.close('all')

## Question 3

In [ ]:
mod = pysces.model('massaction_fixedA', '.')

In [ ]:
mod.doSim(end=0.5, points=30)

In [ ]:
mod.SimPlot()

In [ ]:
mod.sim[-5:]

Towards the end of the simulation, both B and C are 15.15, A is fixed at 5

In [ ]:
# plotting the mass action ratio
fig, ax = plt.subplots()
ax.plot(mod.sim.Time, mod.sim.B*mod.sim.C/5)
ax.set_xlabel('Time (s)')
ax.set_ylabel('$\Gamma$')

$\Gamma$ strives towards 46, i.e. the value of Keq.

In [ ]:
plt.close('all')

In [ ]:
# increase value of kr to 1
mod.kr = 1.0
mod.doSim(end=0.5, points=30)
mod.SimPlot()

In [ ]:
# plotting the mass action ratio
fig, ax = plt.subplots()
ax.plot(mod.sim.Time, mod.sim.B*mod.sim.C/5)
ax.set_xlabel('Time (s)')
ax.set_ylabel('$\Gamma$')

$\Gamma$ now strives to a value of 23, which is the new Keq (kf/kr).

## Question 4

In [ ]:
df1 = pd.read_csv('A.csv', names=['A', 'rate'])
df2 = pd.read_csv('BC.csv', names=['B', 'C', 'rate'])

In [ ]:
df1.tail()

In [ ]:
df1.plot(x='A', y='rate', kind='scatter')

In [ ]:
df2.tail()

### Fitting kf (4b)

In [ ]:
def vf(A, kf):
    return kf*A

In [ ]:
#using lmfit
from lmfit import Model
mymod = Model(vf)
mypar  = mymod.make_params(kf=1)

In [ ]:
myfit = mymod.fit(df1.rate, mypar, A=df1.A)

In [ ]:
myfit

### Fitting kr (4c)

In [ ]:
def vr(B, C, kr):
    return -kr*B*C

In [ ]:
#using lmfit
from lmfit import Model
mymod = Model(vr, independent_vars=['B', 'C'])
mypar  = mymod.make_params(kr=1)

In [ ]:
myfit = mymod.fit(df2.rate, mypar, B=df2.B, C=df2.C)

In [ ]:
myfit

**Plot the data**

In [ ]:
fig = plt.figure()
ax = fig.add_subplot(111, projection='3d')
ax.scatter(df2.B, df2.C, df2.rate)
ax.set_xlabel('B')
ax.set_ylabel('C')
ax.set_zlabel('rate')

### Fitting all data (4d)

**Combining data**

In [ ]:
# combine data
df1['B'] = 0
df1['C'] = 0
df1.tail()

In [ ]:
df2['A'] = 0
df2.tail()

In [ ]:
df3 = pd.concat([df1, df2])

In [ ]:
df3.head()

In [ ]:
df3.tail()

**Fitting**

In [ ]:
def vtot(A, B, C, kf, kr):
    return kf*A - kr*B*C

In [ ]:
#using lmfit
from lmfit import Model
mymod = Model(vtot, independent_vars=['A', 'B', 'C'])
mypar  = mymod.make_params(kf=1, kr=1)

In [ ]:
myfit = mymod.fit(df3.rate, mypar, A=df3.A, B=df3.B, C=df3.C)

In [ ]:
myfit